# Record3D Point Cloud Visualization

This notebook visualizes combined point clouds from all cameras to check alignment.


In [1]:
%load_ext autoreload
%autoreload

In [9]:
!pip install -q scikit-learn matplotlib
!pip install -q plotly
!pip install -q open3d --ignore-installed blinker
!pip install -q --upgrade Pillow
 
    
import sys
import os
from pathlib import Path
import numpy as np
import torch

path = os.getcwd() + "workspace/Home_Reconstruction/scene/"
sys.path.append(path)
path = os.getcwd() + "workspace/Home_Reconstruction/"
sys.path.append(path)

from data_loaders.record3d_loader import Record3DScene
from objectgs_model import ObjectGSModel

# For notebook visualization
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
%matplotlib inline


[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip


## Load Scene


In [10]:
scene_path = Path("/workspace/Home_Reconstruction/data_scenes/maria bedroom")

#Load Scene
scene = Record3DScene(
    scene_path=scene_path,
)


# Create ObjectGS model from scene point cloud
model = ObjectGSModel(
    point_cloud=scene.points,
    colors=scene.colors,
    object_ids=None,  # All set to 1
    voxel_size=0.08,
    k=10
)

Loaded metadata from /workspace/Home_Reconstruction/data_scenes/maria bedroom/EXR_RGBD/metadata.json
  Image dimensions: 720x960
  Number of frames: 9720

Dataset split:
  Training: 486 frames
  Testing: 97 frames

Creating 486 cameras...
Created 486 cameras

Creating 97 cameras...
Created 97 cameras

Loading point cloud...
Loading point cloud from /workspace/Home_Reconstruction/data_scenes/maria bedroom/processed.ply
  Loaded 533,494 points
Scene initialized with 533,494 points

Initializing ObjectGS model:
  Point cloud: 533,494 points
  Voxel size: 0.08m
  Gaussians per anchor: 10
  Number of objects: 2
  Created 8162 anchors
  Total Gaussians: 81,620


In [5]:
# In your notebook, run this to reload:
import importlib
import vis_tools.pc_viewer
importlib.reload(vis_tools.pc_viewer)
from vis_tools.pc_viewer import *

# Now it should work:
visualize_pointclouds(
    "/workspace/Home_Reconstruction/data_scenes/maria bedroom",
    ["processed.ply"]
)


Loading 1 point cloud(s) from maria bedroom

Loading processed.ply...
  ✓ 533,494 points




Summary:
processed.ply                     533,494 points (150,000 displayed)



In [27]:
# Downsample for faster visualization
if len(combined_points) > 50000:
    print(f"Downsampling from {len(combined_points)} to 50k points for visualization...")
    indices = np.random.choice(len(combined_points), 50000, replace=False)
    vis_points = combined_points[indices]
    vis_colors = combined_colors[indices]
else:
    vis_points = combined_points
    vis_colors = combined_colors

# Create 3D plot
fig = plt.figure(figsize=(12, 10))
ax = fig.add_subplot(111, projection='3d')

# Plot point cloud
ax.scatter(vis_points[:, 0], vis_points[:, 1], vis_points[:, 2], 
           c=vis_colors, s=0.1, alpha=0.6)

# Plot camera positions
train_positions = np.array([pos for label, pos in camera_positions if label == 'train'])
test_positions = np.array([pos for label, pos in camera_positions if label == 'test'])

if len(train_positions) > 0:
    ax.scatter(train_positions[:, 0], train_positions[:, 1], train_positions[:, 2],
               c='red', s=50, marker='^', label='Training cameras', alpha=0.8)
if len(test_positions) > 0:
    ax.scatter(test_positions[:, 0], test_positions[:, 1], test_positions[:, 2],
               c='green', s=50, marker='^', label='Test cameras', alpha=0.8)

ax.set_xlabel('X (m)')
ax.set_ylabel('Y (m)')
ax.set_zlabel('Z (m)')
ax.set_title('Combined Point Cloud - Check Alignment')
ax.legend()
ax.set_box_aspect([1,1,1])  # Equal aspect ratio

plt.tight_layout()
plt.show()


NameError: name 'combined_points' is not defined

In [ ]:
!pip install -q gsplat
import sys
from pathlib import Path
sys.path.insert(0, '/workspace/Home_Reconstruction')

from data_loaders.record3d_loader import Record3DScene
from scene.objectgs_model import ObjectGSModel
from train import GaussianTrainer


# Load scene
scene = Record3DScene(
    scene_path=Path("/workspace/Home_Reconstruction/data_scenes/maria bedroom")
)

# Create model
model = ObjectGSModel(
    point_cloud=scene.points,
    colors=scene.colors,
    voxel_size=0.05,
    k=10
)

# Config
config = {
    'lr': 0.0001,
    'num_iterations': 5000,
    'save_interval': 1000,
    'test_interval': 500
}

# Train
trainer = GaussianTrainer(model, scene, config)
trainer.train()

# Render tests
trainer.render_test_sequence()

# Or render single view
trainer.render_single(scene.test_cameras[0], save_path="test.png")